<a href="https://www.kaggle.com/code/mikedelong/visualize-essay-sentences-with-umap-embedding?scriptVersionId=158604867" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
%env TOKENIZERS_PARALLELISM=false
!pip install --quiet keybert
print('pip install keybert complete.')

env: TOKENIZERS_PARALLELISM=false
pip install keybert complete.


In [2]:
import pandas as pd
from nltk.tokenize import sent_tokenize

ESSAYS = '/kaggle/input/aeon-essays-dataset/essays.csv'
USECOLS = ['title', 'description', 'essay', 'authors', ]
df = pd.read_csv(filepath_or_buffer=ESSAYS, usecols=USECOLS)
# split the essay data into sentences 
s = df['essay'].apply(func=sent_tokenize, ).apply(pd.Series, 1).stack()
s.index = s.index.droplevel(-1)
s.name = 'essay'
df = df.drop(columns=['essay']).join(s)
# for performance reasons we need to take a sample
# we have lots of options for taking samples, so let's pick one that will
# yield a relatively small number of classes
# df = df.sample(n=20000, random_state=2024)
df = df.sample(frac=1).sort_values(by='title').head(n=20000)
df.head()

title                                        description  \
1344  Addiction  Addiction changes the brain but it’s not a dis...   
1344  Addiction  Addiction changes the brain but it’s not a dis...   
1807  Addiction  The new science of addiction makes 12-step pro...   
1407  Addiction  Most addicts just stop using in time, without ...   
1772  Addiction  Cutting brings relief because emotion and pain...   

             authors                                              essay  
1344      Marc Lewis     Anxiety, meanwhile, draws attention to threat.  
1344      Marc Lewis  Johnny grew up anxious but competent; he marri...  
1807    Rebecca Ruiz  Addiction, moreover, often exists in tandem wi...  
1407  Stacey McKenna  With a curt nod, I stepped back, heels clackin...  
1772   Carrie Arnold  Compared against 47 controls, the individuals ...

In [3]:
from arrow import now
from keybert import KeyBERT
from sklearn.feature_extraction.text import TfidfVectorizer

MAX_DF = 1.0
MIN_DF = 4
MODEL = 'all-MiniLM-L12-v2'
STOP_WORDS = 'english'
DOCS = df['essay'].values.tolist()

model_start = now()
model = KeyBERT(model=MODEL,)
# model.max_seq_length = 
vectorizer = TfidfVectorizer(ngram_range=(1, 1), stop_words=STOP_WORDS, min_df=MIN_DF, max_df=MAX_DF, )
document_embeddings, word_embeddings = model.extract_embeddings(docs=DOCS, vectorizer=vectorizer, )
print('embedding time: {}'.format(now() - model_start))
print('we have {} documents and {} words.'.format(len(document_embeddings), len(word_embeddings)))
keywords = model.extract_keywords(docs=DOCS, top_n=1, stop_words=STOP_WORDS, vectorizer=vectorizer,
                                  doc_embeddings=document_embeddings, word_embeddings=word_embeddings, min_df=MIN_DF, )
print('model time: {}'.format(now() - model_start))
df['keyword'] = [keyword[0][0] if len(keyword) else '-none-' for keyword in keywords]

.gitattributes:   0%|          | 0.00/1.18k [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/573 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/352 [00:00<?, ?B/s]

train_script.py:   0%|          | 0.00/13.2k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

embedding time: 0:06:14.180094
we have 20000 documents and 9548 words.
model time: 0:06:43.681455


In [4]:
df['title'].value_counts()

title
Anthropology          6537
Animals and humans    4691
Architecture          3401
Archaeology           2328
Addiction             1791
Art                    637
Ageing and death       615
Name: count, dtype: int64

We have chosen to sample out of a small number of titles, so we have fewer buckets to put documents in; and by breaking our essays into sentences we should get vectors that represent fewer words than using the full essays; as a result we expect to see obvious clusters in our scatter plot below rather than something random.

In [5]:
import pandas as pd
from plotly.express import scatter
from umap import UMAP

IGNORE = {'-none-', }

umap_start = now()
df['short text'] = df['essay'].apply(func=lambda x: ' '.join(x.split()[:20]) + '...' if len(x.split()) > 20 else x)
umap_model = UMAP(n_components=2, random_state=2024, verbose=False, n_jobs=1)
df[['u0', 'u1']] = umap_model.fit_transform(X=document_embeddings)
scatter(data_frame=df[~df['keyword'].isin(IGNORE)].sort_values(by='title'), x='u0', y='u1', hover_name='short text',
        hover_data=['keyword', 'title', 'description', 'authors'],
        color = 'title', height=900
       ).show()
print('UMAP time: {}'.format(now() - umap_start))

UMAP time: 0:00:53.217964


We see more concentrated clusters in this analysis because we have shorter documents and fewer classes to put them in; but we also see that the middle part of our graph is dominated by documents where the model assigns them somewhat generic keywords that could be as easily in one class or another. 